In [ ]:
import pandas as pd
import psycopg2

from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain_community.document_loaders import DataFrameLoader
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_community.vectorstores import FAISS
from datetime import datetime



### Retrieve Speeches

In [ ]:
# db_connection -----------------------------------------------------------
con_details = {
    "host"      : "localhost",
    "database"  : "next",
    "user"      : "postgres",
    "password"  : "postgres",
    "port"      : "5433"
}
con = psycopg2.connect(**con_details)

# get data tables ---------------------------------------------------------
df = pd.read_sql_query("""SELECT s.id,s.speech_content,s.date,f.abbreviation AS party
                        FROM open_discourse.speeches AS s
                        INNER JOIN open_discourse.factions AS f ON
                        s.faction_id = f.id;""", con)

### Process speeches

In [ ]:
print(set(df['party'].to_list()))

In [ ]:
# Removing keys from interruptions of a speech
df["speech_content"].replace("\({\d+}\)", "", inplace=True, regex=True) 
df['date'] = pd.to_datetime(df['date'])
df

In [ ]:
# Convert to proper time format
df['date'] = pd.to_datetime(df['date'])


id                                     speech_content       date  \
0             0  Meine Damen und Herren! Ich eröffne die 2. Sit... 1949-09-12   
1             1    Der Bundesrat ist versammelt, Herr Präsident.\n 1949-09-12   
2             2  Ich danke für diese Erklärung. Ich stelle dami... 1949-09-12   
3             3                         Ja, ich habe den Wunsch.\n 1949-09-12   
4             4  Ich erteile dem Herrn Bundespräsidenten das Wo... 1949-09-12   
...         ...                                                ...        ...   
930955  1084268                        \n\nWir sind zwar Kollegen. 2022-12-16   
930956  1084269          \n\nLiebe, sehr geehrte Frau Präsidentin! 2022-12-16   
930957  1084270                                   \n\nVielen Dank. 2022-12-16   
930958  1084272  \n\nDen Abschluss dieser Aktuellen Stunde bild... 2022-12-16   
930959  1084273  \n\nSehr geehrte Frau Präsidentin! Werte Kolle... 2022-12-16   

            party  
0       not found  
1       not found  
2       not found  
3       not found  
4       not found  
...           ...  
930955  not found  
930956    CDU/CSU  
930957  not found  
930958  not found  
930959        SPD  

[930960 rows x 4 columns]

In [27]:
def split_documents(df, min_chunk_size=100):
    """
    Load documents from a DataFrame, split them into smaller chunks for vector storage and remove chunks of small size.

    Parameters
    ----------
    df : pandas.DataFrame
        A DataFrame containing the documents to be processed, with a column named 'speech_content'.
    min_chunk_size : int, optional
        Minimum number of characters a chunk must have to be included in the result. Default is 100.

    Returns
    -------
    list
        A list of split document chunks ready for further processing or vectorization.
    """
    # Initialize a DataFrameLoader with the given DataFrame and specify the column containing the content to load
    loader = DataFrameLoader(data_frame=df, page_content_column='speech_content')
    # Load the data from the DataFrame into a suitable format for processing
    data = loader.load()
    # Initialize a RecursiveCharacterTextSplitter to split the text into chunks
    splitter = RecursiveCharacterTextSplitter(
        chunk_size=1024,
        chunk_overlap=32,
        length_function=len,
        is_separator_regex=False,
    )
    # Split the loaded data into smaller chunks using the splitter
    documents = splitter.split_documents(documents=data)
    # Discard small chunks below the threshold
    cleaned_documents = [doc for doc in documents if len(doc.page_content) >= min_chunk_size]

    return cleaned_documents

In [ ]:
# Define starting dates of legislature periods
dates = ["1953-10-06", "1957-10-16", "1961-10-17", "1965-10-19", "1969-10-20", "1972-12-13", "1976-12-14", "1980-11-04", "1983-03-29", "1987-02-18","1990-12-20", "1994-11-10", "1998-10-26", "2002-10-17", "2005-10-18", "2009-10-27", "2013-10-22","2017-10-24","2021-10-26", None]
# Load sentence transformer 
embeddings = HuggingFaceEmbeddings(model_name="paraphrase-multilingual-MiniLM-L12-v2")

# Create vector store for all speaches
# Split text into documents for vectorstore
documents = split_documents(df)
# Create and save faiss vectorstorage
index_name = 'speeches_1949_09_12'
db = FAISS.from_documents(documents, embeddings)
db.save_local(folder_path="FAISS", index_name=index_name)
print("Sucessfully created vector store for all legislature")

# Create vector store for each legislature
# loop parameters
period = 1
previous_date = None

# Iterate over all date to split by legislature getting vector stores for each period
for date in dates:
    if previous_date is None:
        legislature_df = df.loc[df['date'] < datetime.strptime(date, "%Y-%m-%d")]
    elif date is None:
        legislature_df = df.loc[df['date'] >= datetime.strptime(previous_date, "%Y-%m-%d")]
    else:
        legislature_df = df.loc[(df['date'] >= datetime.strptime(previous_date, "%Y-%m-%d")) & (df['date'] < datetime.strptime(date, "%Y-%m-%d"))]

   
    # Split text into documents for vectorstore
    documents = split_documents(legislature_df)

    # Create and save faiss vectorstorage
    index_name = f'{period}_legislature'
    db = FAISS.from_documents(documents, embeddings)
    db.save_local(folder_path="FAISS", index_name=index_name)
    print(f"Sucessfully created vector store for {period}. legislature")

    # Change loop parameters for next iteration
    period += 1
    previous_date = date


    


c:\Python\Lib\site-packages\huggingface_hub\file_download.py:1132: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


Sucessfully created vector store for 1. legislature
Sucessfully created vector store for 2. legislature
Sucessfully created vector store for 3. legislature
Sucessfully created vector store for 4. legislature
Sucessfully created vector store for 5. legislature
Sucessfully created vector store for 6. legislature
Sucessfully created vector store for 7. legislature
Sucessfully created vector store for 8. legislature
Sucessfully created vector store for 9. legislature
Sucessfully created vector store for 10. legislature
Sucessfully created vector store for 11. legislature
Sucessfully created vector store for 12. legislature
Sucessfully created vector store for 13. legislature
Sucessfully created vector store for 14. legislature
Sucessfully created vector store for 15. legislature
Sucessfully created vector store for 16. legislature
Sucessfully created vector store for 17. legislature
Sucessfully created vector store for 18. legislature
Sucessfully created vector store for 19. legislature
Su

This data has been uploaded to: https://huggingface.co/datasets/TomData/test